In [119]:
from ngsolve import*
from ngsolve.webgui import Draw
from netgen.occ import*
from netgen.webgui import Draw as DrawGeo
import numpy as np
from math import pi
import time 
import scipy.sparse as sp

############################################################
order=2
nu=1e-1    
h0=0.1
############
t = Parameter(0.)
mesh=Mesh(unit_square.GenerateMesh(maxh=h0))#####
p1=pi
p2=pi
exact_u =CoefficientFunction( (sin(2*pi* x)*cos(2*pi*y), -cos(2*pi*x)*sin(2*pi*y)))
u_1= sin(2*pi* x)*cos(2*pi*y)
u_2=-cos(2*pi*x)*sin(2*pi*y)
u_1x=2*p1*cos(2*p1*x)*cos(2*p1*y)
u_1xx = -4*p1*p1*sin(2*p1*x)*cos(2*p1*y) 
u_1y=-2*p1*sin(2*p1*x)*sin(2*p1*y)
u_1yy = -4*p1*p1*sin(2*p1*x)*cos(2*p1*y) 
u_2x=2*p1*sin(2*p1*x)*sin(2*p1*y)
u_2xx = 4*p1*p1*cos(2*p1*x)*sin(2*p1*y)  
u_2y=-2*p1*cos(2*p1*x)*cos(2*p1*y)
u_2yy = 4*p1*p1*cos(2*p1*x)*sin(2*p1*y) 
exact_u0 =CoefficientFunction( (u_1x,u_1y))
exact_u1=CoefficientFunction( (u_2x,u_2y ))
exact_p = CoefficientFunction((   (cos(4*pi*x)+cos(4*pi*y)) )   )
p_x= (-4*pi*sin(4*pi*x))
p_y=(-4*pi*sin(4*pi*y)) 
exact_f_Brinkman=CoefficientFunction((u_1-nu*(u_1xx+u_1yy)+p_x,  u_2-nu*(u_2xx+u_2yy)+p_y))
####################################################################################
VT = HDiv(mesh, order=order, dirichlet="bottom|right|top|left",  highest_order_dc=True,  dgjumps=True)#####Relaxed BDM space
VF=TangentialFacetFESpace(mesh,order=order, dirichlet="bottom|right|top|left", highest_order_dc=True)
Q = L2(mesh, order=order-1)
N1 = FESpace("number",mesh)
X = VT*VF*Q*N1


u, uhat, p, lam1= X.TrialFunction()
v, vhat, q, mu1= X.TestFunction()



n = specialcf.normal(mesh.dim)
h = specialcf.mesh_size
dS = dx(element_boundary=True)

gfu = GridFunction(X)

#######算子定义
def tang(vec):
    return vec - (vec*n)*n
#########
stokes =nu*InnerProduct(Grad(u), Grad(v))*dx \
    + nu*InnerProduct(Grad(u)*n, tang(vhat-v))*dS \
    + nu*InnerProduct(Grad(v)*n, tang(uhat-u))*dS \
    + nu*5*(order*order/h)* InnerProduct(tang(vhat-v), tang(uhat-u))*dS \
   -InnerProduct(div(u), q)*dx -InnerProduct(div(v), p)*dx+(p * mu1 + lam1 * q)*dx
a = BilinearForm(X,bonus_intorder=5*order+4)
a += stokes
a.Assemble()
exact_f_Brinkman=CoefficientFunction((u_1-nu*(u_1xx+u_1yy)+p_x,  u_2-nu*(u_2xx+u_2yy)+p_y))
f = LinearForm(X,bonus_intorder=12)
f+=exact_f_Brinkman*v*dx(bonus_intorder=12)
f.Assemble()
#####
VT.Average(f.vec)




############################################################   mass  matrices
#fes = VectorValued(FESpace("nonconforming", mesh))
fesbdm = HDiv(mesh, order=order)
ubdm,vbdm = fesbdm.TnT()
conv11 = ConvertOperator(VT,  fesbdm)   # conversion from VT to bdm
massbdm = BilinearForm(ubdm*vbdm*dx).Assemble().mat
massp1 = conv11.CreateTranspose() @ massbdm  @ conv11  # multiplies sparse matrices

###################################
combined_mat = a.mat.CreateMatrix()
#combined_mat.AsVector().data = a.mat.AsVector()+massp1.AsVector()


inv_combined_mat = combined_mat.Inverse(X.FreeDofs(), inverse="pardiso")

#########
gfu.components[0].Set(exact_u, definedon=mesh.Boundaries("bottom|right|top|left"))
gfu.components[1].Set(tang(exact_u), definedon=mesh.Boundaries("bottom|right|top|left"))
gfu.vec.data += inv_combined_mat*(f.vec- combined_mat*gfu.vec)
####
velocity = CoefficientFunction(gfu.components[0])
err_u =  sqrt(Integrate( (velocity-exact_u)*(velocity-exact_u), mesh))
print ( "%.2e & %.2e \\" % (order,err_u))

4.00e+00 & 4.86e-02 \
